In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

In [ ]:
!pip install google-cloud-speech


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 285.0/285.0 kB 7.8 MB/s eta 0:00:00


In [ ]:
!pip install pydub

In [ ]:
# Import Libraries and Set Up Google Cloud Client
import os
from google.cloud import speech_v1p1beta1 as speech
import io
import pandas as pd
from pydub.utils import mediainfo
from tqdm import tqdm
from pydub import AudioSegment
from IPython.display import Audio, display
import concurrent.futures
import difflib


os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = '/content/drive/MyDrive/audio_files/modified-return-352819-377e8de8ce2c.json'




In [ ]:
import os

audio_folder_path = '/content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/'
print(os.listdir(audio_folder_path))


['44 BEATIFY', '01 CHORD', '22 SUBTLE', '14 NAIVE', '11 COURTEOUS', '10 DEBT', '05 BOUQUET', '21 HIATUS', '33 DRACHM', '31 FACADE', '19 RADIX', '35 PLACEBO', '36 ABSTEMIOUS', '13 EQUIVOCAL', '28 BANAL', '06 PSALM', '29 QUADRUPED', '25 GOUGE', '20 ASSIGNATE', '39 PUERPERAL', '12 RAREFY', '34 AEON', '17 THYME', '42 TOPIARY', '08 DENY', '40 AVER', '07 CAPON', '16 GAOLED', '04 AISLE', '47 DEMESNE', '03 DEPOT', '09 NAUSEA', '23 PROCREATE', '49 LABILE', '27 SIMILE', '15 CATACOMB', '30 CELLIST', '38 IDYLL', '18 HEIR', '43 LEVIATHAN', '02 ACHE', '46 SIDEREAL', '37 DETENTE', '48 SYNCOPE', '32 ZEALOT', '50 CAMPANILE', '41 GAUCHE', '24 GIST', '26 SUPERFLUOUS', '45 PRELATE']


In [ ]:
# Initialize the client
client = speech.SpeechClient()


# transcribe audio files
def transcribe_audio(file_path):
    try:
        print(f"Processing file: {file_path}")

        # audio file information
        info = mediainfo(file_path)
        sample_rate = int(info['sample_rate'])

        with io.open(file_path, "rb") as audio_file:
            content = audio_file.read()

        if not content:
            print(f"File {file_path} is empty or not read correctly")
            return file_path, None

        audio = speech.RecognitionAudio(content=content)
        config = speech.RecognitionConfig(
            encoding=speech.RecognitionConfig.AudioEncoding.LINEAR16,
            enable_automatic_punctuation=True,
            audio_channel_count=1,
            language_code="en-US",
        )

        response = client.recognize(config=config, audio=audio)
        transcripts = [result.alternatives[0].transcript for result in response.results]

        transcription = " ".join(transcripts)
        print(f"Transcription for {file_path}: {transcription}")
        return file_path, transcription
    except Exception as e:
        print(f"Error processing file {file_path}: {e}")
        return file_path, None



audio_folder_path = '/content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71'
audio_files = []
for root, dirs, files in os.walk(audio_folder_path):
    for file in files:
        if file.endswith(".wav"):
            audio_files.append(os.path.join(root, file))

# files
print(f"Audio files found: {len(audio_files)}")

if not audio_files:
    print("No audio files found in the specified folder.")





Audio files found: 3500


In [ ]:
# transcribe audio files with progress bar and concurrent processing
transcriptions = {}
with concurrent.futures.ThreadPoolExecutor() as executor:
    futures = {executor.submit(transcribe_audio, file): file for file in audio_files}
    for future in tqdm(concurrent.futures.as_completed(futures), total=len(audio_files), desc="Transcribing audio files"):
        file_path, transcription = future.result()
        transcriptions[file_path] = transcription

# some transcriptions
for file, transcription in list(transcriptions.items())[:5]:
    print(f"File: {file}\nTranscription: {transcription}\n")

Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP16.wav
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP51.wav
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP28.wav
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP52.wav
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP19.wav
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP37.wav


Transcribing audio files:   0%|          | 1/3500 [00:02<2:00:52,  2.07s/it]

Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP52.wav: defy
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP4.wav


Transcribing audio files:   0%|          | 4/3500 [00:02<24:30,  2.38it/s]

Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP19.wav: Do you have to try?
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP15.wav
Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP37.wav: speedify
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP3.wav
Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP16.wav: Beach Boy
Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP20.wav
Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP51.wav: beatified

...

Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/45 PRELATE/PP51.wav: prelate


Transcribing audio files: 100%|█████████▉| 3499/3500 [14:29<00:00,  4.81it/s]

Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/45 PRELATE/PP45.wav: prelate
Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/45 PRELATE/PP40.wav: prelate
Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/45 PRELATE/PP67.wav: prelate


Transcribing audio files: 100%|██████████| 3500/3500 [14:29<00:00,  4.03it/s]

Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/45 PRELATE/PP48.wav: prelate
File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP52.wav
Transcription: defy

File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP19.wav
Transcription: Do you have to try?

File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP37.wav
Transcription: speedify

File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP16.wav
Transcription: Beach Boy

File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP51.wav
Transcription: beatified



In [ ]:
# Test the function with a single audio file
test_audio_file = '/content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP50.wav'
transcription = transcribe_audio(test_audio_file)
print(f"Transcription: {transcription}")

Processing file: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP50.wav
Transcription for /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP50.wav: beatified
Transcription: ('/content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/44 BEATIFY/PP50.wav', 'beatified')


In [ ]:
expected_words = ['ZEALOT', 'PRELATE', 'CAMPANILE', 'SIDEREAL', 'ACHE', 'SUPERFLUOUS', 'DETENTE', 'SYNCOPE', 'GIST', 'GAUCHE',
                  'CELLIST', 'LABILE', 'CATACOMB', 'SIMILE', 'LEVIATHAN', 'IDYLL', 'HEIR', 'DEPOT', 'NAUSEA', 'PROCREATE',
                  'AVER', 'AEON', 'GAOLED', 'THYME', 'DENY', 'RAREFY', 'AISLE', 'CAPON', 'TOPIARY', 'DEMESNE', 'RADIX',
                  'PUERPERAL', 'GOUGE', 'EQUIVOCAL', 'PLACEBO', 'PSALM', 'BANAL', 'ASSIGNATE', 'ABSTEMIOUS', 'QUADRUPED',
                  'CHORD', 'DEBT', 'DRACHM', 'COURTEOUS', 'BOUQUET', 'FACADE', 'NAIVE', 'BEATIFY', 'SUBTLE', 'HIATUS']


# check similarity
def is_similar(transcribed_word, target_word, threshold=0.5):
    return difflib.SequenceMatcher(None, transcribed_word, target_word).ratio() > threshold


# transcriptions with expected words
results = []
for file, transcription in transcriptions.items():
    result = {}
    if transcription is not None:
        # Convert transcription to lowercase for comparison
        words = transcription.lower().split()
        for word in expected_words:
            result[word] = 0
            for transcribed_word in words:
                if is_similar(transcribed_word, word.lower()):
                    result[word] = 1
                    break
    else:
        for word in expected_words:
            result[word] = 0

    result['file'] = os.path.basename(file)
    results.append(result)

# DataFrame from the results
df = pd.DataFrame(results, index=[os.path.basename(f) for f in transcriptions.keys()])
df.set_index('file', inplace=True)
df.to_csv('transcription_results.csv')


print(df)




          ZEALOT  PRELATE  CAMPANILE  SIDEREAL  ACHE  SUPERFLUOUS  DETENTE  \
file                                                                         
PP52.wav       0        0          0         0     0            0        0   
PP19.wav       0        0          0         0     0            0        0   
PP37.wav       0        0          0         0     0            0        0   
PP16.wav       0        0          0         0     1            0        0   
PP51.wav       0        0          0         0     0            0        0   
...          ...      ...        ...       ...   ...          ...      ...   
PP51.wav       0        1          0         0     0            0        0   
PP45.wav       0        1          0         0     0            0        0   
PP40.wav       0        1          0         0     0            0        0   
PP67.wav       0        1          0         0     0            0        0   
PP48.wav       0        1          0         0     0            

In [ ]:
# play some of the transcribed audio files
print("\nPlaying some audio files with their transcriptions:\n")
sample_audio_files = list(transcriptions.keys())[800:825]

for file in sample_audio_files:
    print(f"File: {file}\nTranscription: {transcriptions[file]}\n")
    display(Audio(file))


Playing some audio files with their transcriptions:

File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP62.wav
Transcription: placebo



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP42.wav
Transcription: placebo



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP66.wav
Transcription: placebo



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP50.wav
Transcription: placebo



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP46.wav
Transcription: Kersey Valley



...

File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP44.wav
Transcription: placebo



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP28.wav
Transcription: 



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP60.wav
Transcription: gazebo



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP10.wav
Transcription: placebo



File: /content/drive/MyDrive/audio_files/Dataset 1 (Cleaned with Separated Words)/NART Words Ss 1 to 71/35 PLACEBO/PP13.wav
Transcription: received



In [ ]:
# play some of the incorrect transcriptions
print("\nSome Incorrect Transcriptions:\n")
incorrect_samples = {file: transcription for file, transcription in transcriptions.items() if "Could not understand audio" in transcription or "Error" in transcription}

for i, (file, transcription) in enumerate(list(incorrect_samples.items())[200:250]):
    print(f"File: {file}\nTranscription: {transcription}\n")
    display(Audio(file))


Some Incorrect Transcriptions:

